# Finite Element Code from Sheet 5

In [1]:
import numpy as np
import matplotlib.pyplot as plt
import scipy.sparse as sp
import scipy.sparse.linalg as spla


In [3]:
# Criss-cross grid 
def crisscrossgrid(n):
    x,y = np.meshgrid(np.linspace(0,1,n+1), np.linspace(0,1,n+1))
    x = np.reshape(x,[(n+1)**2,1])
    y = np.reshape(y,[(n+1)**2,1])
    coordinates = np.hstack([x,y])
    elements = []
    for j in range(n):
        for k in range(n):
            elements.append([j*(n+1)+k, j*(n+1)+k+1, (j+1)*(n+1)+k+1])
            elements.append([j*(n+1)+k, (j+1)*(n+1)+k+1, (j+1)*(n+1)+k])
    elements=np.asarray(elements)
    boundarynodes = []
    for j in range(n+1):
        boundarynodes.append(j)
        boundarynodes.append(n*(n+1)+j)
    for j in range(1,n):
        boundarynodes.append(j*(n+1))
        boundarynodes.append(j*(n+1)+n)
    return coordinates, elements, boundarynodes

def assemble_stiffness_local(cornercoordinates):
    # cornercoordinates = coordinates of the corner as array [[x0, y0],[x1,y1],[x2,y2]]
    # G and B as in exercise 2 
    G = np.linalg.solve(np.vstack([[1,1,1],cornercoordinates.T]), np.array([[0,0],[1,0],[0,1]]))
    B = np.vstack([cornercoordinates[1,:]-cornercoordinates[0,:],cornercoordinates[2,:]-cornercoordinates[0,:]])
    A_T = 0.5*abs(np.linalg.det(B))*G.dot(G.T)
    return A_T

def assemble_mass_local(cornercoordinates):
    # see exercise 2 for the formulas 
    B = np.vstack([cornercoordinates[1,:]-cornercoordinates[0,:],cornercoordinates[2,:]-cornercoordinates[0,:]])
    M_T = abs(np.linalg.det(B))*np.array([[1/12, 1/24, 1/24],[1/24, 1/12, 1/24],[1/24, 1/24, 1/12]])
    return M_T

def assemble_load_local(cornercoordinates, ffun):
    # see exercise 2 for the formulas
    B = np.vstack([cornercoordinates[1,:]-cornercoordinates[0,:],cornercoordinates[2,:]-cornercoordinates[0,:]])
    return abs(np.linalg.det(B))*ffun(np.sum(cornercoordinates[:,],0)/3)*np.ones(3)/6


def assemble_stiffness(elements,coordinates):
    # empty sparse matrix 
    A = sp.lil_matrix((len(coordinates),len(coordinates)))
    
    # loop over all elements: add contributions of all local stiffness matrices 
    for idx in elements:
        A[tuple(np.meshgrid(idx,idx))] += assemble_stiffness_local(coordinates[idx,:])
    return sp.csr_matrix(A)

def assemble_mass(elements,coordinates):
    M = sp.lil_matrix((len(coordinates),len(coordinates)))
    # loop over all elements: add contributions of all local mass matrices
    for idx in elements:
        M[tuple(np.meshgrid(idx,idx))] += assemble_mass_local(coordinates[idx,:])
    return sp.csr_matrix(M)   

def assemble_load(elements,coordinates,ffun):
    f = np.zeros(len(coordinates))
    # loop over all ements: add contributions of all local load vectors
    for idx in elements:
        f[idx] += assemble_load_local(coordinates[idx,:],ffun)
    return f

def solve(elements,coordinates,ffun,dirichletboundary):
    # assemble stiffness matrix and load vector 
    A = assemble_stiffness(elements,coordinates)
    f = assemble_load(elements,coordinates,ffun)
    
    # set all entries of the solution vector to zero (in particular those on the Dirichlet boundary)
    v = np.zeros(len(coordinates))
    
    # determine free nodes and values of the solution on the free nodes 
    freenodes = list(set(range(len(coordinates)))-set(dirichletboundary))
    v[freenodes] = spla.spsolve(A[tuple(np.meshgrid(freenodes,freenodes))],f[freenodes])
    return v 